# Réseaux de neurones et classification d'images

Le but de ce TP est de comparer l'architecture *Perceptron multi-couche* et *Réseau à convolution* pour la classification d'images, d'abord sur un corpus d'images simples en noir et blanc, puis sur un corpus plus complexe d'images en couleur.


Le but du TP est de remplir les zones de code vides pour implémenter un programme qui peut classer correctement les images (avec un taux d'erreur de 10% maximum)

Remplacer ci-dessous par les noms, prénoms numéros d'étudiants pour le binôme

NOM1 PRENOM1 NUM-ETU1

NOM2 PRENOM2 NUM-ETU2


## Imports

In [ ]:
import torch
from torch.utils.data import Dataset, DataLoader


from torchvision import datasets
from torchvision.transforms import ToTensor, Compose, Resize
import matplotlib.pyplot as plt


## Le corpus Fashion MNIST

Ce corpus est constitué d'images en noir et blanc de taille $28\times28$.
Ces images représentent des vêtements réparties en 10 classes différentes.

Notez bien que même si ces images peuvent être représentées par une matrice  $28\times28$, elles sont en faites stockées comme des tenseurs $1\times28\times28$ de façon à expliciter qu'au lieu des habituels 3 canaux RGB, on n'a ici qu'un seul canal qui indique le niveau de gris.

In [ ]:

training_data = datasets.FashionMNIST(
    root="data",
    train=True,
    download=True,
    transform=ToTensor()
)


train_val_ratio = 0.8
train_size = int(train_val_ratio * len(training_data))
val_size = len(training_data) - train_size
training_data, val_data = torch.utils.data.random_split(training_data, [train_size, val_size])


test_data = datasets.FashionMNIST(
    root="data",
    train=False,
    download=True,
    transform=ToTensor()
)

NB_CLASSES=10

labels_map = {
    0: "T-Shirt",
    1: "Trouser",
    2: "Pullover",
    3: "Dress",
    4: "Coat",
    5: "Sandal",
    6: "Shirt",
    7: "Sneaker",
    8: "Bag",
    9: "Ankle Boot",
}

figure = plt.figure(figsize=(8, 8))
cols, rows = 5,2
for i in range(1, cols * rows + 1):
    sample_idx = torch.randint(len(training_data), size=(1,)).item()
    img, label = training_data[sample_idx]
    figure.add_subplot(rows, cols, i)
    plt.title(labels_map[label])
    plt.axis("off")
    plt.imshow(img.squeeze(), cmap="gray")
plt.show()


## On charge les données

In [ ]:
BATCH_SIZE=512

train_dataloader = DataLoader(training_data, batch_size=BATCH_SIZE, shuffle=True, pin_memory=True)
val_dataloader = DataLoader(val_data, batch_size=BATCH_SIZE, shuffle=False, pin_memory=True)
test_dataloader = DataLoader(test_data, batch_size=BATCH_SIZE, shuffle=False, pin_memory=True)


In [ ]:
# Display image and label.
train_iter = iter(train_dataloader) #get an iterator over data
train_features, train_labels = next(train_iter) # get a batch of data
print(f"Feature batch shape: {train_features.size()}")
print(f"Labels batch shape: {train_labels.size()}")
img = train_features[0].squeeze() # reformat the first pic as 28x28
label = train_labels[0]
plt.imshow(img, cmap="gray") #it's B&W
plt.show()
print(f"Label: {label}")

Que contient notre image ?

In [ ]:
print(img)

## Évaluation



In [ ]:
def eval(net, dataloader, device, epoch):

  total_test = 0.0
  correct_test = 0.0

  net.eval()

  #iterate over data
  for local_batch, local_labels in dataloader:
    # Transfer to GPU
    local_batch, local_labels = local_batch.to(device), local_labels.to(device)

    preds = net(local_batch)
    total_test += preds.size(0)
    correct_test += (torch.argmax(preds, dim=1) == local_labels).sum()

  print(f"Epoch: {epoch}, Test accuracy: {correct_test/total_test}")


## Implémentation d'un Perceptron multicouche

Implementer la class MLP pour les perceptrons multicouches.

Le constructeur prend en entrée:
- *input_size* la taille du vecteur d'entrée
- *hidden_sizes* la liste des tailles des couches internes
- *output_size* la taille de la couche de sortie
- *activation* la classe qui implémente la fonction à appliquer après chaque transformation linéaire

Aide: vous pouvez utiliser la classe **Sequential** pour modéliser la liste des transformations de votre MLP

La fonction forward prend entrée une image. Il faut d'abord transformer l'image (le tenseur à 3 dimensions) en un vecteur, puis on applique successivement chaque transformation linéaire, suivie d'une activation si on n'est pas sur la dernière couche.

In [ ]:
class MLP(torch.nn.Module):

  def __init__(self, input_size, hidden_sizes, output_size, activation):
    super().__init__()

    #your code begins here
    pass
    #your code ends here

  def forward(self,x):
    #your code begins here
    pass
    #your code ends here


## Boucle d'entraînement

In [ ]:
def train(net, optimizer, epochs, trainloader, valloader, testloader, batch_size, device, eval_frq=10):

  loss_fn = torch.nn.CrossEntropyLoss()

  total_loss = 0.0

  n_batches = 0
  for epoch in range(epochs):

    net.train()
    # iterate through train data
    #   -> get new batch
    #   -> send it to device
    #   -> compute class scores with net
    #   -> compute loss and compute the gradient of the loss
    #   -> call step() on optimizer to perform SGD, reset gradients to zero

    #your code begins here
    pass
    #your code ends here

    # eval if it's time...
    if epoch % eval_frq == 0:
      print(f"Epoch: {epoch}, Mean loss: {total_loss/n_batches}")
      eval(net, valloader, device, epoch)


### Entraînement d'un modèle MLP

Si tout est correct, voud devriez avoir un MLP qui arrive à 90% de classifications correctes.

In [ ]:
net = MLP(28*28, [512, 256], NB_CLASSES, torch.nn.ReLU)
opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader=val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


## Un premier réseau à convolutions

Implémenter la classe pour le CNN qui implémente les étapes suivantes:
- *convolution 1* qui transforme chaque point (1 canal $\to$ 10 canaux) en regardant son voisinage de taille $5\times5$. Régler le *padding* pour que l'image de sortie ait la même taille ($28\times28$) que l'entrée
- *max-pooling 1* qui prend pour chaque canal la plus grande valeur dans un carré de taille $2\times2$. Essayer ensuite de changer la valeur du paramètre  *stride* à $2$.
- *convolution 2* qui transforme chaque point (10 canaux $\to$ 20 canaux) en regardant son voisinage de taille $5\times5$. Régler le *padding* pour que l'image de sortie ait la taille $10\times10$
- *max-pooling 2* qui prend pour chaque canal la plus grande valeur dans un carré de taille $2\times2$. Essayer ensuite de changer la valeur du paramètre  *stride* à $2$.
- *convolution 3* qui transforme chaque point (20 canaux $\to$ 40 canaux) en regardant son voisinage de taille $3\times3$. Régler le *padding* pour que l'image de sortie ait la taille $3\times3$
- *max-pooling 3* qui prend pour chaque canal la plus grande valeur dans un carré de taille $3\times3$.
- un MLP qui a pour taille de couches internes (en plus de la couche d'entrée et la taille de sortie) $128$ et $64$.






In [ ]:
class ConvNetFM(torch.nn.Module):
  def __init__(self,):
    super().__init__()

    #your code begins here
    self.c1 = None
    self.m1 = None
    self.c2 = None
    self.m2 = None
    self.c3 = None
    self.m3 = None
    self.mlp = None
    #your code ends here

  def forward(self,x):
    #print(x.size())
    x = self.c1(x)
    x = self.m1(x)
    x = self.c2(x)
    x = self.m2(x)
    x = self.c3(x)
    x = self.m3(x)
    x = self.mlp(x)
    return x

Vous devriez obtenir aussi une exactitude à 90% avec ce réseau.
Sur des petites images sans couleur, MLP et ConvNet se valent.

In [ ]:
net = ConvNetFM()

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


# Le corpus CIFAR10

On va maintenant appliquer et adapter nos classificateurs à des images couleurs de taille $32\times32$ où chaque point a pour commencer 3 canaux d'information qui correspondent aux intensités RGB (rouge,vert,bleu)

In [ ]:

training_data = datasets.CIFAR10(
    root="data",
    train=True,
    download=True,
    transform=ToTensor()
)

test_data = datasets.CIFAR10(
    root="data",
    train=False,
    download=True,
    transform=ToTensor()
)

In [ ]:
NB_CLASSES=10

labels_map ={
    0:"airplane",
    1:"automobile",
    2:"bird",
    3:"cat",
    4: "deer",
    5: "dog",
    6: "frog",
    7: "horse",
    8: "ship",
    9: "truck"
}

figure = plt.figure(figsize=(8, 8))
cols, rows = 5,2
for i in range(1, cols * rows + 1):
    sample_idx = torch.randint(len(training_data), size=(1,)).item()
    img, label = training_data[sample_idx]
    figure.add_subplot(rows, cols, i)
    plt.title(labels_map[label])
    plt.axis("off")
    plt.imshow(img.permute(1,2,0)) #quizz question: why permute ?
plt.show()


In [ ]:

train_dataloader = DataLoader(training_data, batch_size=BATCH_SIZE, shuffle=True, pin_memory=True)
test_dataloader = DataLoader(test_data, batch_size=BATCH_SIZE, shuffle=False, pin_memory=True)


In [ ]:
# Display image and label.
train_iter = iter(train_dataloader)
train_features, train_labels = next(train_iter)
print(f"Feature batch shape: {train_features.size()}")
print(f"Labels batch shape: {train_labels.size()}")
img = train_features[0].squeeze()
label = train_labels[0]
plt.imshow(img.permute(1,2,0))
plt.show()
print(f"Label: {label}")

In [ ]:
train_features, train_labels = next(train_iter)
print(f"Feature batch shape: {train_features.size()}")
print(f"Labels batch shape: {train_labels.size()}")
img = train_features[0].squeeze()
label = train_labels[0]
plt.imshow(img.permute(1,2,0))
plt.show()
print(f"Label: {label}")

In [ ]:
print(img)

## Classification avec un MLP

Créer l'objet MLP (tailles intermédiaires $1024,512,256$)

In [ ]:
#your code begins here
net = MLP(?????, [1024, 512, 256], ????, torch.nn.ReLU)
#your code ends here

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


## Classification avec convolutions


Adapter la classe pour le CNN qui implémente les étapes suivantes:
- *convolution 1* qui transforme chaque point (3 canaux $\to$ 10 canaux) en regardant son voisinage de taille $5\times5$. Régler le *padding* pour que l'image de sortie ait la même taille ($32\times32$) que l'entrée
- *max-pooling 1* qui prend pour chaque canal la plus grande valeur dans un carré de taille $2\times2$. Mettre la valeur du paramètre  *stride* à $2$.
- *convolution 2* qui transforme chaque point (10 canaux $\to$ 20 canaux) en regardant son voisinage de taille $5\times5$. Régler le *padding* pour que l'image de sortie ait la taille $12\times12$
- *max-pooling 2* qui prend pour chaque canal la plus grande valeur dans un carré de taille $2\times2$. Mettre la valeur du paramètre  *stride* à $2$.
- *convolution 3* qui transforme chaque point (20 canaux $\to$ 40 canaux) en regardant son voisinage de taille $3\times3$. Régler le *padding* pour que l'image de sortie ait la taille $4\times4$
- *max-pooling 3* qui prend pour chaque canal la plus grande valeur dans un carré de taille $4\times4$.
- un MLP qui a pour taille de couches internes (en plus de la couche d'entrée et la taille de sortie) $128$ et $64$.


In [ ]:
class ConvNet(torch.nn.Module):
  def __init__(self,):
    super().__init__()

    #your code begins here
    self.c1 = None
    self.m1 = None
    self.c2 = None
    self.m2 = None
    self.c3 = None
    self.m3 = None
    self.mlp = None
    #your code ends here

  def forward(self,x):
    #print(x.size())
    x = self.c1(x)
    x = self.m1(x)
    x = self.c2(x)
    x = self.m2(x)
    x = self.c3(x)
    x = self.m3(x)
    x = self.mlp(x)
    return x

In [ ]:
net = ConvNet()

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


## Une autre architecture pour les convolutions

On va s'inspirer d'une architecture plus récente (VGG, https://arxiv.org/pdf/1409.1556.pdf) pour les réseaux à convolutions.

L'idée est de construire le réseaux à partir de *blocs* constitués de deux convolutions successives, suivies d'un *pooling*.
Chaque nouveau bloc double le nombre de canaux par rapport au bloc précédent. Finalement un MLP transforme l'image obtenu à la fin du dernier bloc en un vecteur de scores pour les classes.


Nous allons implémenter cette architecture pour 1,2,3 blocs.






### VGG "1 bloc"

Implémenter la classe VGG1.
Le module est constitué de:
- *conv 1-1* une convolution $3$ canaux $\to$ $32$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille que la l'image d'entrée ($32\times32$)
- *activ-1* une activation élémentaire, ici ReLU
- *conv 1-2* une convolution $32$ canaux $\to$ $32$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille que la l'image d'entrée ($32\times32$)
- *pooling 1*  un *pooling* $\max$ sur une fenêtre de $2\times2$
- un MLP avec couches internes de tailles $128,64$.



In [ ]:
class VGG1(torch.nn.Module):
  def __init__(self,):
    super().__init__()

    #your code begins here
    self.c11 = None
    self.c12 = None
    self.m1 = None
    self.mlp = None
    #your code ends here

  def forward(self,x):
    #print(x.size())
    x = self.c11(x)
    x = torch.relu(x)
    x = self.c12(x)
    x = self.m1(x)
    x = self.mlp(x)
    return x


In [ ]:
net = VGG1()

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


### VGG "2 blocs"

Implémenter la classe VGG2.
Le module est constitué de:
- de *conv 1-1*, *conv 1-2* et *pooling 1* comme dans VGG1
- *conv 2-1* une convolution $32$ canaux $\to$ $64$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille que la l'image en entrée du 2e bloc
- *activ-2* une activation
- *conv 2-2* une convolution $64$ canaux $\to$ $64$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille
- *pooling 2*  un *pooling* $\max$ sur une fenêtre de $2\times2$
- un MLP avec couches internes de tailles $128,64$.


In [ ]:
class VGG2(torch.nn.Module):
  def __init__(self,):
    super().__init__()

    #your code begins here
    self.c11 = None
    self.c12 = None
    self.m1 = None

    self.c21 = None
    self.c22 = None
    self.m2 = None

    self.mlp = None
    #your code ends here

  def forward(self,x):
    #print(x.size())
    x = self.c11(x)
    x = torch.relu(x)
    x = self.c12(x)
    x = self.m1(x)
    x = self.c21(x)
    x = torch.relu(x)
    x = self.c22(x)
    x = self.m2(x)
    x = self.mlp(x)
    return x

In [ ]:
net = VGG2()

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)


### VGG "3 blocs"

Implémenter la classe VGG3.
Le module est constitué de:
- de *conv 1-1*, *conv 1-2*, *pooling 1*, *conv 2-1*, *conv 2-2*, *pooling 2*comme dans VGG2
- *conv 3-1* une convolution $64$ canaux $\to$ $128$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille que la l'image en entrée du 2e bloc
- *activ-3* l'activation
- *conv 3-2* une convolution $128$ canaux $\to$ $128$ canaux, avec un voisinage de taille $3\times3$ avec un padding réglé pour que l'image de sortie ait la même taille
- *pooling 3*  un *pooling* $\max$ sur une fenêtre de $2\times2$
- un MLP avec couches internes de tailles $128,64$.


In [ ]:
class VGG2(torch.nn.Module):
  def __init__(self,):
    super().__init__()

    #your code begins here
    self.c11 = None
    self.c12 = None
    self.m1 = None

    self.c21 = None
    self.c22 = None
    self.m2 = None

    self.c31 = None
    self.c32 = None
    self.m3 = None

    self.mlp = None
    #your code ends here

  def forward(self,x):
    #print(x.size())
    x = self.c11(x)
    x = torch.relu(x)
    x = self.c12(x)
    x = self.m1(x)
    x = self.c21(x)
    x = torch.relu(x)
    x = self.c22(x)
    x = self.m2(x)
    x = self.c31(x)
    x = torch.relu(x)
    x = self.c32(x)
    x = self.m3(x)
    x = self.mlp(x)
    return x

Avec ce dernier modèle, vous devriez atteindre 75% d'exactitude

In [ ]:
net = VGG3()

opt = torch.optim.Adam(net.parameters(),lr=0.001)

use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")
net = net.to(device)

train(net, opt, epochs=50, trainloader=train_dataloader, valloader= val_dataloader, testloader=test_dataloader, batch_size=BATCH_SIZE, device=device, eval_frq=5)
